# Let's Explore the Data!

In [1]:
# Set project root to path
import sys
from pathlib import Path

# Get the absolute path to the project root
current_dir = Path().absolute()
project_root = current_dir.parent if 'notebooks' in str(current_dir) else current_dir

# Add the project root to Python path
if str(project_root) not in sys.path:
    sys.path.insert(0, str(project_root))

print(f"Project root added to path: {project_root}")

Project root added to path: d:\Projects\PORTF_2_German_Energy_forcast\german-energy-forcast


## Load Forecasting Exploratory Data Analysis

This notebook explores the patterns and characteristics of electrical load data in Germany, focusing on actual vs forecasted loads.

### 1. Setup and Data Loading

First, let's import necessary libraries and load 

In [2]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
import scipy.stats as stats
from pathlib import Path
import holidays
from datetime import datetime


# Load the data
data_dir = Path('D:/Projects/PORTF_2_German_Energy_forcast/german-energy-forcast/data/raw')
load_forecast_df = pd.read_csv(data_dir / 'load_data_20240217_20250216.csv', index_col=0)

# Properly convert index to datetime with timezone handling
load_forecast_df.index = pd.to_datetime(load_forecast_df.index, utc=True)
load_forecast_df.index = load_forecast_df.index.tz_convert('Europe/Berlin')

In [3]:
# Print analysis period and basic info
print(f"Analysis Period: {load_forecast_df.index.min()} to {load_forecast_df.index.max()}")
print("\nDataset Shape:", load_forecast_df.shape)
print("\nColumns:", load_forecast_df.columns.tolist())
print("\nMissing Values:")
print(load_forecast_df.isnull().sum())

Analysis Period: 2024-02-17 00:00:00+01:00 to 2025-02-15 23:45:00+01:00

Dataset Shape: (35047, 2)

Columns: ['Forecasted Load', 'Actual Load']

Missing Values:
Forecasted Load    0
Actual Load        7
dtype: int64


## 2. Hourly Load Distribution Analysis

Let's analyze how the load is distributed across different hours of the day.

##### 2.1. Histogram of load values

In [4]:
# Histogram of load values with enhanced styling
fig1 = go.Figure()
fig1.add_trace(
    go.Histogram(
        x=load_forecast_df['Actual Load'],
        name='Actual Load',
        nbinsx=50,
        marker=dict(
            color='#2ecc71',
            line=dict(color='#27ae60', width=1)
        ),
        opacity=0.75
    )
)

fig1.update_layout(
    template='plotly_dark',  # Ensure dark theme
    title=dict(
        text="Distribution of Electricity Load in Germany",
        font=dict(size=20, color='white'),
        x=0.5,
        y=0.95
    ),
    xaxis=dict(
        title=dict(
            text="Load (MW)",
            font=dict(size=14, color='white')
        ),
        gridcolor='rgba(128, 128, 128, 0.2)',
        tickformat=',.0f',
        separatethousands=True,
        color='white'  # Changed from bgcolor to color
    ),
    yaxis=dict(
        title=dict(
            text="Frequency",
            font=dict(size=14, color='white')
        ),
        gridcolor='rgba(128, 128, 128, 0.2)',
        color='white'  # Changed from bgcolor to color
    ),
    plot_bgcolor='rgb(17, 17, 17)',  # Dark background matching MkDocs
    paper_bgcolor='rgb(17, 17, 17)',  # Dark background matching MkDocs
    height=480,
    width=900,
    margin=dict(l=60, r=30, t=60, b=60),
    showlegend=False,
    bargap=0.1
)

# Add subtitle
fig1.add_annotation(
    text='Historical Data Analysis (2022-2023)',
    xref='paper',
    yref='paper',
    x=0.5,
    y=1.05,
    showarrow=False,
    font=dict(size=14, color='#7f8c8d'),
    xanchor='center'
)

# Add mean line
mean_load = load_forecast_df['Actual Load'].mean()
fig1.add_vline(
    x=mean_load,
    line_dash="dash",
    line_color="#e74c3c",
    annotation_text=f"Mean: {mean_load:,.0f} MW",
    annotation_position="top right",
    annotation_font_color="#e74c3c",
    annotation_font_size=12
)

# Save with explicit configuration
fig1.write_html(
    "load_distribution.html",
    include_plotlyjs=True,
    full_html=False,
    config={'responsive': True}
)

fig1.show()

##### 2.2. Box plots for each hour

In [5]:

fig2 = go.Figure()
fig2.add_trace(
    go.Box(
        x=load_forecast_df.index.hour,
        y=load_forecast_df['Actual Load'],
        name='Hourly Distribution',
        marker_color='#3498db'
    )
)
fig2.update_layout(
    template='plotly_dark',
    title_text="Load Distribution by Hour",
    xaxis_title="Hour of Day",
    yaxis_title="Load (MW)",
    height=500,
    width=800
)
fig2.show()


##### 2.3. Statistical summary by hour

In [6]:
fig3 = go.Figure()
hourly_stats = load_forecast_df.groupby(load_forecast_df.index.hour)['Actual Load'].agg(['mean', 'median', 'std'])

fig3.add_trace(
    go.Scatter(
        x=hourly_stats.index,
        y=hourly_stats['mean'],
        name='Mean',
        line=dict(color='#2ecc71')
    )
)
fig3.add_trace(
    go.Scatter(
        x=hourly_stats.index,
        y=hourly_stats['median'],
        name='Median',
        line=dict(color='#3498db')
    )
)
fig3.add_trace(
    go.Scatter(
        x=hourly_stats.index,
        y=hourly_stats['mean'] + hourly_stats['std'],
        name='Mean + Std',
        line=dict(color='#e74c3c', dash='dash')
    )
)
fig3.update_layout(
    template='plotly_dark',
    title_text="Statistical Summary by Hour",
    xaxis_title="Hour of Day",
    yaxis_title="Load (MW)",
    height=500,
    width=800
)
fig3.show()

##### 2.4. Density plots comparing weekday vs weekend load distribution

In [7]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def create_time_based_distributions(df):
    # Create figure with subplots
    fig = make_subplots(rows=2, cols=1, 
                       subplot_titles=('Day vs Night Distribution', 
                                     'Weekday vs Weekend Distribution'))
    
    # 1. Day vs Night Analysis
    day_hours = df[df.index.hour.isin(range(9, 20))]['Actual Load']  # 9 AM to 8 PM
    night_hours = df[~df.index.hour.isin(range(9, 20))]['Actual Load']  # Night hours
    
    # Day-Night Distribution
    fig.add_trace(
        go.Histogram(x=day_hours, name='Day Hours', 
                    nbinsx=50, opacity=0.7),
        row=1, col=1
    )
    fig.add_trace(
        go.Histogram(x=night_hours, name='Night Hours', 
                    nbinsx=50, opacity=0.7),
        row=1, col=1
    )
    
    # 2. Weekday vs Weekend Analysis
    weekday_data = df[~df.index.weekday.isin([5,6])]['Actual Load']
    weekend_data = df[df.index.weekday.isin([5,6])]['Actual Load']
    
    # Weekday-Weekend Distribution
    fig.add_trace(
        go.Histogram(x=weekday_data, name='Weekday', 
                    nbinsx=50, opacity=0.7),
        row=2, col=1
    )
    fig.add_trace(
        go.Histogram(x=weekend_data, name='Weekend', 
                    nbinsx=50, opacity=0.7),
        row=2, col=1
    )
    
    # Update layout
    fig.update_layout(
        template='plotly_dark',
        height=800,
        width=1000,
        barmode='overlay',
        showlegend=True
    )
    
    return fig

# Create and save the plot
fig = create_time_based_distributions(load_forecast_df)
fig.show()
# Print summary statistics
print("\nSummary Statistics:")
print("\nDay Hours (9 AM - 8 PM):")
print(load_forecast_df[load_forecast_df.index.hour.isin(range(9, 20))]['Actual Load'].describe())
print("\nNight Hours:")
print(load_forecast_df[~load_forecast_df.index.hour.isin(range(9, 20))]['Actual Load'].describe())
print("\nWeekday:")
print(load_forecast_df[~load_forecast_df.index.weekday.isin([5,6])]['Actual Load'].describe())
print("\nWeekend:")
print(load_forecast_df[load_forecast_df.index.weekday.isin([5,6])]['Actual Load'].describe())


Summary Statistics:

Day Hours (9 AM - 8 PM):
count    16060.000000
mean     58280.630012
std       7611.056364
min      34869.000000
25%      53507.250000
50%      58832.000000
75%      63389.250000
max      76582.000000
Name: Actual Load, dtype: float64

Night Hours:
count    18980.000000
mean     48438.955005
std       7885.277239
min      32300.000000
25%      42508.500000
50%      47206.500000
75%      53645.250000
max      75515.000000
Name: Actual Load, dtype: float64

Weekday:
count    24960.000000
mean     55590.594351
std       8843.001350
min      32748.000000
25%      48360.750000
50%      56840.000000
75%      61952.500000
max      76582.000000
Name: Actual Load, dtype: float64

Weekend:
count    10080.000000
mean     46410.421528
std       6268.488312
min      32300.000000
25%      41893.750000
50%      46089.500000
75%      50572.250000
max      63605.000000
Name: Actual Load, dtype: float64


## 3. Anomaly Detection in Load Data

### 3.1. Extreme Load Values Analysis

We identify extreme values using statistical methods and visualize them to understand their patterns and potential causes.


In [8]:
def analyze_extreme_loads(df, percentile_threshold=0.01):
    """
    Analyze extreme load values using percentile thresholds
    """
    # Calculate thresholds
    high_threshold = df['Actual Load'].quantile(1 - percentile_threshold)
    low_threshold = df['Actual Load'].quantile(percentile_threshold)
    
    # Identify extreme values
    extremes = df[
        (df['Actual Load'] > high_threshold) | 
        (df['Actual Load'] < low_threshold)
    ].copy()
    
    # Create visualization
    fig = go.Figure()
    
    # Add all load points
    fig.add_trace(go.Scatter(
        x=df.index,
        y=df['Actual Load'],
        mode='markers',
        name='Normal Load',
        marker=dict(color='blue', size=2, opacity=0.5)
    ))
    
    # Add extreme points
    fig.add_trace(go.Scatter(
        x=extremes.index,
        y=extremes['Actual Load'],
        mode='markers',
        name='Extreme Load',
        marker=dict(color='red', size=5)
    ))
    
    # Add threshold lines
    fig.add_hline(y=high_threshold, line_dash="dash", line_color="red",
                  annotation_text=f"High threshold: {high_threshold:.0f} MW")
    fig.add_hline(y=low_threshold, line_dash="dash", line_color="red",
                  annotation_text=f"Low threshold: {low_threshold:.0f} MW")
    
    fig.update_layout(
        template='plotly_dark',
        title='Load Values with Extreme Points Highlighted',
        xaxis_title='Date',
        yaxis_title='Load (MW)',
        height=500,
        width=800,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01
        )
    )
    
    fig.show()
    # Print summary
    print("\nExtreme Load Analysis:")
    print(f"High threshold (99th percentile): {high_threshold:.0f} MW")
    print(f"Low threshold (1st percentile): {low_threshold:.0f} MW")
    print(f"Number of extreme high loads: {len(extremes[extremes['Actual Load'] > high_threshold])}")
    print(f"Number of extreme low loads: {len(extremes[extremes['Actual Load'] < low_threshold])}")
    
    return extremes

# Analyze extreme loads
extremes = analyze_extreme_loads(load_forecast_df)



Extreme Load Analysis:
High threshold (99th percentile): 71885 MW
Low threshold (1st percentile): 35371 MW
Number of extreme high loads: 351
Number of extreme low loads: 351


## 3.2 holiday_pattern Analysis


In [9]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import holidays
from datetime import datetime

def analyze_holiday_impact(df):
    """
    Analyze load patterns during holidays
    """
    # Get German holidays
    de_holidays = holidays.DE()
    
    # Convert index to datetime if it's not already
    if not isinstance(df.index, pd.DatetimeIndex):
        df.index = pd.to_datetime(df.index)
    
    # Create is_holiday column
    df = df.copy()  # Create a copy to avoid SettingWithCopyWarning
    df['is_holiday'] = [date.date() in de_holidays for date in df.index]
    
    # Calculate average daily patterns for holidays and non-holidays
    holiday_pattern = df[df['is_holiday']].groupby(df[df['is_holiday']].index.hour)['Actual Load'].mean()
    normal_pattern = df[~df['is_holiday']].groupby(df[~df['is_holiday']].index.hour)['Actual Load'].mean()
    
    # Create visualization
    fig = go.Figure()
    
    # Add patterns
    fig.add_trace(go.Scatter(
        x=list(range(24)),  # Hours 0-23
        y=normal_pattern.values,
        name='Normal Days',
        line=dict(color='blue', width=2)
    ))
    
    fig.add_trace(go.Scatter(
        x=list(range(24)),  # Hours 0-23
        y=holiday_pattern.values,
        name='Holidays',
        line=dict(color='red', width=2)
    ))
    
    fig.update_layout(
        template='plotly_dark',
        title='Average Daily Load Pattern: Holidays vs Normal Days',
        xaxis_title='Hour of Day',
        yaxis_title='Average Load (MW)',
        height=600,
        showlegend=True,
        xaxis=dict(
            tickmode='array',
            ticktext=[f'{i:02d}:00' for i in range(24)],
            tickvals=list(range(24))
        )
    )
    
    # Save plot
    #fig.write_image("holiday_impact.png")
    fig.show()

    # Print summary statistics
    print("\nHoliday Impact Analysis:")
    print(f"Number of holidays: {df['is_holiday'].sum()}")
    print(f"\nAverage load on holidays: {df[df['is_holiday']]['Actual Load'].mean():.0f} MW")
    print(f"Average load on normal days: {df[~df['is_holiday']]['Actual Load'].mean():.0f} MW")
    print(f"Difference: {(df[~df['is_holiday']]['Actual Load'].mean() - df[df['is_holiday']]['Actual Load'].mean()):.0f} MW")
    
    return holiday_pattern, normal_pattern

# Run the analysis
holiday_pattern, normal_pattern = analyze_holiday_impact(load_forecast_df)


Holiday Impact Analysis:
Number of holidays: 864

Average load on holidays: 44025 MW
Average load on normal days: 53175 MW
Difference: 9150 MW


### 3.3. Temperature-load relationship

#### Load weather data

In [13]:
def analyze_weather_data(weather_df):
    """
    Analyze and summarize weather data for all cities
    """
    # Create datetime index if not already
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    # Add 100 to temperature values for correct celsius values
    temp_columns = ['temperature_berlin', 'temperature_hamburg', 'temperature_frankfurt']
    weather_corrected = weather_df.copy()
    for col in temp_columns:
        weather_corrected[col] = weather_df[col] + 100
    
    # Basic information
    print("=== Weather Data Analysis ===")
    print(f"Total data points: {len(weather_df)}")
    print(f"Time range: {weather_df.index.min()} to {weather_df.index.max()}")
    print(f"\nNumber of cities: {len(temp_columns)}")
    
    # Temperature statistics for each city
    print("\nTemperature Statistics (°C):")
    for city in temp_columns:
        print(f"\n{city.replace('temperature_', '').capitalize()}:")
        stats = weather_corrected[city].describe()
        print(f"Min: {stats['min']:.1f}°C")
        print(f"Max: {stats['max']:.1f}°C")
        print(f"Mean: {stats['mean']:.1f}°C")
        print(f"Std: {stats['std']:.1f}°C")
        
        # Count extreme temperatures
        extreme_cold = (weather_corrected[city] < -10).sum()
        extreme_hot = (weather_corrected[city] > 30).sum()
        print(f"Hours below -10°C: {extreme_cold}")
        print(f"Hours above 30°C: {extreme_hot}")

# Load weather data
weather_df = pd.read_csv('D:/Projects/PORTF_2_German_Energy_forcast/german-energy-forcast/data/raw/weather_temperature_20240217_20250216.csv')

# Run analysis
analyze_weather_data(weather_df)
# Load weather data


=== Weather Data Analysis ===
Total data points: 8761
Time range: 2024-02-17 00:00:00+01:00 to 2025-02-16 00:00:00+01:00

Number of cities: 3

Temperature Statistics (°C):

Berlin:
Min: -14.6°C
Max: 22.9°C
Mean: 6.1°C
Std: 6.8°C
Hours below -10°C: 110
Hours above 30°C: 0

Hamburg:
Min: -11.7°C
Max: 105.6°C
Mean: 9.4°C
Std: 6.4°C
Hours below -10°C: 13
Hours above 30°C: 1

Frankfurt:
Min: -17.0°C
Max: 21.0°C
Mean: 6.4°C
Std: 7.3°C
Hours below -10°C: 225
Hours above 30°C: 0


C:\Users\risha\AppData\Local\Temp\ipykernel_11184\3520590205.py:7: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



In [15]:
def plot_temperature_timeline(weather_df):
    """
    Create temperature time series plot for all cities
    """
    # Create datetime index if not already
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    fig = go.Figure()
    
    # Define colors and names for each city
    colors = {
        'temperature_berlin': '#00B5F7',
        'temperature_hamburg': '#FB8B24',
        'temperature_frankfurt': '#53DD6C'
    }
    
    city_names = {
        'temperature_berlin': 'Berlin',
        'temperature_hamburg': 'Hamburg',
        'temperature_frankfurt': 'Frankfurt'
    }
    
    # Plot each city's temperature
    for column in ['temperature_berlin', 'temperature_hamburg', 'temperature_frankfurt']:
        # Add 100 to correct the temperature values
        temp_data = weather_df[column] + 100
        
        fig.add_trace(go.Scatter(
            x=weather_df.index,
            y=temp_data,
            name=city_names[column],
            line=dict(color=colors[column], width=1),
            opacity=0.7
        ))
    
    fig.update_layout(
        template='plotly_dark',
        title='Temperature Variation Over Time Across Major German Cities',
        xaxis_title='Date',
        yaxis_title='Temperature (°C)',
        height=600,
        width=1200,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="right",
            x=0.99,
            bgcolor='rgba(0,0,0,0.3)'
        )
    )
    
    fig.show()
    return fig

weather_df = pd.read_csv('D:/Projects/PORTF_2_German_Energy_forcast/german-energy-forcast/data/raw/weather_temperature_20240217_20250216.csv')


# Create and save the time series plot
fig_timeline = plot_temperature_timeline(weather_df)

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1236900850.py:7: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



# Create a comprehensive analysis to spot weather-related anomalies with multiple perspectives:

In [20]:
def create_load_temp_scatter(load_df, weather_df):
    """
    Create scatter plot of load vs temperature with hour-of-day coloring
    """
    # Create datetime indices
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df = weather_df.copy()
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    if not isinstance(load_df.index, pd.DatetimeIndex):
        load_df = load_df.copy()
        load_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(load_df),
            freq='15T',
            tz='Europe/Berlin'
        )
    
    # 1. Resample load data to hourly
    load_hourly = load_df['Actual Load'].resample('1H').mean()
    
    # 2. Correct temperature (Berlin as example)
    temp_berlin = weather_df['temperature_berlin'] + 100
    
    # 3. Align the indices
    combined_df = pd.DataFrame({
        'Temperature': temp_berlin
    })
    combined_df['Load'] = load_hourly
    combined_df['Hour'] = combined_df.index.hour
    
    # Drop any NaN values
    combined_df = combined_df.dropna()
    
    # Create the scatter plot
    fig = go.Figure()
    
    # Add main scatter plot
    fig.add_trace(go.Scatter(
        x=combined_df['Temperature'],
        y=combined_df['Load'],
        mode='markers',
        marker=dict(
            size=4,
            color=combined_df['Hour'],
            colorscale='Viridis',
            showscale=True,
            colorbar=dict(
                title=dict(
                    text='Hour of Day',
                    side='right'
                )
            ),
            opacity=0.6
        ),
        name='Load vs Temperature'
    ))
    
    # Update layout
    fig.update_layout(
        template='plotly_dark',
        title='Load vs Temperature Relationship (Berlin)',
        xaxis_title='Temperature (°C)',
        yaxis_title='Load (MW)',
        height=700,
        width=700,
        showlegend=False
    )
    
    # Print summary statistics
    print("\nData Summary:")
    print(f"Total points: {len(combined_df)}")
    print(f"Temperature range: {combined_df['Temperature'].min():.1f}°C to {combined_df['Temperature'].max():.1f}°C")
    print(f"Load range: {combined_df['Load'].min():.0f} MW to {combined_df['Load'].max():.0f} MW")
    
    return fig

# Load the data if not already loaded
load_df = pd.read_csv('D:/Projects/PORTF_2_German_Energy_forcast/german-energy-forcast/data/raw/load_data_20240217_20250216.csv')
weather_df = pd.read_csv('D:/Projects/PORTF_2_German_Energy_forcast/german-energy-forcast/data/raw/weather_temperature_20240217_20250216.csv')

# Create and display the scatter plot
fig = create_load_temp_scatter(load_df, weather_df)
fig.show()


Data Summary:
Total points: 8757
Temperature range: -14.6°C to 22.9°C
Load range: 32410 MW to 76252 MW


C:\Users\risha\AppData\Local\Temp\ipykernel_11184\4061407087.py:8: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\4061407087.py:17: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\4061407087.py:25: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



In [24]:
def create_load_temp_scatter_with_trends(load_df, weather_df):
    """
    Create scatter plot with trend lines and seasonal breakdowns
    """
    # Create datetime indices
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df = weather_df.copy()
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    if not isinstance(load_df.index, pd.DatetimeIndex):
        load_df = load_df.copy()
        load_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(load_df),
            freq='15T',
            tz='Europe/Berlin'
        )
    
    # 1. First create separate series with proper indices
    load_hourly = load_df['Actual Load'].resample('1H').mean()
    temp_berlin = pd.Series(weather_df['temperature_berlin'] + 100, index=weather_df.index)
    
    # 2. Create a DataFrame with aligned data
    combined_df = pd.DataFrame(index=weather_df.index)
    combined_df['Temperature'] = temp_berlin
    combined_df['Load'] = load_hourly
    combined_df['Hour'] = combined_df.index.hour
    combined_df['Month'] = combined_df.index.month
    
    # Drop any NaN values
    combined_df = combined_df.dropna()
    
    # Add season column
    combined_df['Season'] = pd.cut(combined_df['Month'], 
                                 bins=[0, 3, 6, 9, 12],
                                 labels=['Winter', 'Spring', 'Summer', 'Fall'])
    
    # Create subplots
    fig = make_subplots(rows=2, cols=2,
                       subplot_titles=('All Seasons', 'Winter (Dec-Feb)',
                                     'Summer (Jun-Aug)', 'Spring/Fall'),
                       vertical_spacing=0.15,
                       horizontal_spacing=0.1)
    
    # Plot 1: All data with trend line
    fig.add_trace(
        go.Scatter(x=combined_df['Temperature'],
                  y=combined_df['Load'],
                  mode='markers',
                  marker=dict(size=4,
                            color=combined_df['Hour'],
                            colorscale='Viridis',
                            showscale=True,
                            opacity=0.6),
                  name='All Data'),
        row=1, col=1
    )
    
    # Add trend line
    z = np.polyfit(combined_df['Temperature'], combined_df['Load'], 2)
    p = np.poly1d(z)
    x_trend = np.linspace(combined_df['Temperature'].min(), 
                         combined_df['Temperature'].max(), 100)
    fig.add_trace(
        go.Scatter(x=x_trend,
                  y=p(x_trend),
                  mode='lines',
                  line=dict(color='red', width=3),
                  name='Trend'),
        row=1, col=1
    )
    
    # Plot 2: Winter
    winter_data = combined_df[combined_df['Season'] == 'Winter']
    fig.add_trace(
        go.Scatter(x=winter_data['Temperature'],
                  y=winter_data['Load'],
                  mode='markers',
                  marker=dict(size=4,
                            color=winter_data['Hour'],
                            colorscale='Viridis',
                            showscale=False,
                            opacity=0.6),
                  name='Winter'),
        row=1, col=2
    )
    
    # Plot 3: Summer
    summer_data = combined_df[combined_df['Season'] == 'Summer']
    fig.add_trace(
        go.Scatter(x=summer_data['Temperature'],
                  y=summer_data['Load'],
                  mode='markers',
                  marker=dict(size=4,
                            color=summer_data['Hour'],
                            colorscale='Viridis',
                            showscale=False,
                            opacity=0.6),
                  name='Summer'),
        row=2, col=1
    )
    
    # Plot 4: Spring/Fall combined
    spring_fall_data = combined_df[combined_df['Season'].isin(['Spring', 'Fall'])]
    fig.add_trace(
        go.Scatter(x=spring_fall_data['Temperature'],
                  y=spring_fall_data['Load'],
                  mode='markers',
                  marker=dict(size=4,
                            color=spring_fall_data['Hour'],
                            colorscale='Viridis',
                            showscale=False,
                            opacity=0.6),
                  name='Spring/Fall'),
        row=2, col=2
    )
    
    # Update layout
    fig.update_layout(
        template='plotly_dark',
        title='Load vs Temperature Relationship by Season (Berlin)',
        height=800,
        width=1000,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="right",
            x=0.99
        )
    )
    
    # Update all x and y axes labels
    for i in range(1, 3):
        for j in range(1, 3):
            fig.update_xaxes(title_text='Temperature (°C)', row=i, col=j)
            fig.update_yaxes(title_text='Load (MW)', row=i, col=j)
    
    # Print summary statistics
    print("\nData Summary by Season:")
    for season in combined_df['Season'].unique():
        season_data = combined_df[combined_df['Season'] == season]
        print(f"\n{season}:")
        print(f"Temperature range: {season_data['Temperature'].min():.1f}°C to {season_data['Temperature'].max():.1f}°C")
        print(f"Load range: {season_data['Load'].min():.0f} MW to {season_data['Load'].max():.0f} MW")
        print(f"Number of points: {len(season_data)}")
    
    return fig

# Create and display the plot
fig = create_load_temp_scatter_with_trends(load_df, weather_df)
fig.show()


Data Summary by Season:

Winter:
Temperature range: -13.3°C to 16.9°C
Load range: 32660 MW to 76252 MW
Number of points: 2160

Spring:
Temperature range: -14.6°C to 22.9°C
Load range: 33002 MW to 67258 MW
Number of points: 2180

Summer:
Temperature range: -11.5°C to 22.8°C
Load range: 32410 MW to 65824 MW
Number of points: 2208

Fall:
Temperature range: -5.1°C to 20.7°C
Load range: 35122 MW to 73155 MW
Number of points: 2209


C:\Users\risha\AppData\Local\Temp\ipykernel_11184\2193004919.py:8: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\2193004919.py:17: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\2193004919.py:25: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



In [25]:
def create_hour_load_temp_heatmap(load_df, weather_df):
    """
    Create heatmap with hours on x-axis, temperature on y-axis, and load as color
    """
    # Create datetime indices
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df = weather_df.copy()
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    if not isinstance(load_df.index, pd.DatetimeIndex):
        load_df = load_df.copy()
        load_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(load_df),
            freq='15T',
            tz='Europe/Berlin'
        )
    
    # Resample load data to hourly
    load_hourly = load_df['Actual Load'].resample('1H').mean()
    
    # Create DataFrame with aligned data
    combined_df = pd.DataFrame(index=weather_df.index)
    combined_df['Temperature'] = weather_df['temperature_berlin'] + 100
    combined_df['Load'] = load_hourly
    combined_df['Hour'] = combined_df.index.hour
    combined_df['Month'] = combined_df.index.month
    
    # Drop any NaN values
    combined_df = combined_df.dropna()
    
    # Create pivot table for heatmap
    # Round temperature to nearest integer for better visualization
    combined_df['Temperature_rounded'] = combined_df['Temperature'].round()
    pivot_data = combined_df.pivot_table(
        values='Load',
        index='Temperature_rounded',
        columns='Hour',
        aggfunc='mean'
    )
    
    # Create the heatmap
    fig = go.Figure(data=go.Heatmap(
        z=pivot_data.values,
        x=pivot_data.columns,  # Hours
        y=pivot_data.index,    # Temperature
        colorscale='Viridis',
        colorbar=dict(title='Average Load (MW)'),
    ))
    
    # Update layout
    fig.update_layout(
        template='plotly_dark',
        title='Average Load by Hour and Temperature (Berlin)',
        xaxis_title='Hour of Day',
        yaxis_title='Temperature (°C)',
        height=800,
        width=1200,
    )
    
    # Add more x-axis ticks (every hour)
    fig.update_xaxes(tickmode='linear', tick0=0, dtick=1)
    
    # Print summary statistics
    print("\nData Summary:")
    print(f"Temperature range: {combined_df['Temperature'].min():.1f}°C to {combined_df['Temperature'].max():.1f}°C")
    print(f"Load range: {combined_df['Load'].min():.0f} MW to {combined_df['Load'].max():.0f} MW")
    print(f"Total hours analyzed: {len(combined_df)}")
    
    return fig

# Create and display the plot
fig = create_hour_load_temp_heatmap(load_df, weather_df)
fig.show()


Data Summary:
Temperature range: -14.6°C to 22.9°C
Load range: 32410 MW to 76252 MW
Total hours analyzed: 8757


C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1020455753.py:8: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1020455753.py:17: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1020455753.py:25: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.



In [26]:
def create_seasonal_hour_temp_heatmaps(load_df, weather_df):
    """
    Create seasonal heatmaps with hours on x-axis, temperature on y-axis, and load as color
    """
    # Create datetime indices
    if not isinstance(weather_df.index, pd.DatetimeIndex):
        weather_df = weather_df.copy()
        weather_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(weather_df),
            freq='1H',
            tz='Europe/Berlin'
        )
    
    if not isinstance(load_df.index, pd.DatetimeIndex):
        load_df = load_df.copy()
        load_df.index = pd.date_range(
            start='2024-02-17',
            periods=len(load_df),
            freq='15T',
            tz='Europe/Berlin'
        )
    
    # Prepare data
    load_hourly = load_df['Actual Load'].resample('1H').mean()
    combined_df = pd.DataFrame(index=weather_df.index)
    combined_df['Temperature'] = weather_df['temperature_berlin'] + 100
    combined_df['Load'] = load_hourly
    combined_df['Hour'] = combined_df.index.hour
    combined_df['Month'] = combined_df.index.month
    
    # Add season
    combined_df['Season'] = pd.cut(combined_df['Month'], 
                                 bins=[0, 3, 6, 9, 12],
                                 labels=['Winter', 'Spring', 'Summer', 'Fall'])
    
    # Round temperature for better visualization
    combined_df['Temperature_rounded'] = combined_df['Temperature'].round()
    
    # Create subplots
    fig = make_subplots(
        rows=2, cols=2,
        subplot_titles=('Winter (Dec-Feb)', 'Spring (Mar-May)',
                       'Summer (Jun-Aug)', 'Fall (Sep-Nov)'),
        vertical_spacing=0.15,
        horizontal_spacing=0.1
    )
    
    # Get overall load range for consistent color scale
    load_min = combined_df['Load'].min()
    load_max = combined_df['Load'].max()
    
    # Create heatmap for each season
    for idx, season in enumerate(['Winter', 'Spring', 'Summer', 'Fall']):
        row = (idx // 2) + 1
        col = (idx % 2) + 1
        
        season_data = combined_df[combined_df['Season'] == season]
        pivot_data = season_data.pivot_table(
            values='Load',
            index='Temperature_rounded',
            columns='Hour',
            aggfunc='mean'
        )
        
        fig.add_trace(
            go.Heatmap(
                z=pivot_data.values,
                x=pivot_data.columns,  # Hours
                y=pivot_data.index,    # Temperature
                colorscale='Viridis',
                zmin=load_min,         # Consistent color scale
                zmax=load_max,
                colorbar=dict(title='Average Load (MW)'),
                showscale=(idx == 3)   # Only show colorbar for last plot
            ),
            row=row, col=col
        )
        
        # Update axes labels
        fig.update_xaxes(title_text='Hour of Day', row=row, col=col, tickmode='linear', tick0=0, dtick=3)
        fig.update_yaxes(title_text='Temperature (°C)', row=row, col=col)
    
    # Update layout
    fig.update_layout(
        template='plotly_dark',
        title='Seasonal Load Patterns by Hour and Temperature (Berlin)',
        height=1000,
        width=1200,
    )
    
    # Print summary statistics for each season
    print("\nSeasonal Data Summary:")
    for season in ['Winter', 'Spring', 'Summer', 'Fall']:
        season_data = combined_df[combined_df['Season'] == season]
        print(f"\n{season}:")
        print(f"Temperature range: {season_data['Temperature'].min():.1f}°C to {season_data['Temperature'].max():.1f}°C")
        print(f"Load range: {season_data['Load'].min():.0f} MW to {season_data['Load'].max():.0f} MW")
        print(f"Hours analyzed: {len(season_data)}")
    
    return fig

# Create and display the plots
fig = create_seasonal_hour_temp_heatmaps(load_df, weather_df)
fig.show()


Seasonal Data Summary:

Winter:
Temperature range: -13.3°C to 16.9°C
Load range: 32660 MW to 76252 MW
Hours analyzed: 2160

Spring:
Temperature range: -14.6°C to 22.9°C
Load range: 33002 MW to 67258 MW
Hours analyzed: 2184

Summer:
Temperature range: -11.5°C to 22.8°C
Load range: 32410 MW to 65824 MW
Hours analyzed: 2208

Fall:
Temperature range: -5.1°C to 20.7°C
Load range: 35122 MW to 73155 MW
Hours analyzed: 2209


C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1956506318.py:8: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1956506318.py:17: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.

C:\Users\risha\AppData\Local\Temp\ipykernel_11184\1956506318.py:25: FutureWarning:

'H' is deprecated and will be removed in a future version, please use 'h' instead.

